<a href="https://colab.research.google.com/github/1-Kelvin/moa/blob/peterDataKafkaStream/data-analysis/Data_Analysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Preparation

In [ ]:
#@title Drive Connection
from google.colab import drive
drive.mount('/content/gdrive')
%cd 'gdrive/My Drive/Colab Notebooks/big-data/data'/


Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).
[Errno 2] No such file or directory: 'gdrive/My Drive/Colab Notebooks/big-data/data/'
/content/gdrive/.shortcut-targets-by-id/1_Y7gB4rfipFsUyp7gshd28gJ_okdV6XR/big-data/data


In [ ]:
#@title Manage Imports & Extensions
import os.path
import pandas as pd
import numpy as np
import math
import matplotlib.pyplot as plt
import seaborn as sns
sns.set(rc={'figure.figsize':(15, 4)})
import altair as alt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from pathlib import Path


# pretty prints dataframes
%load_ext google.colab.data_table




The google.colab.data_table extension is already loaded. To reload it, use:
  %reload_ext google.colab.data_table


In [ ]:
# 
# !pip install plotly -U

In [ ]:
#@title Merge Sensor Files
bathroomFiles = ["TA_Bad_1.txt", "TA_Bad_2.txt", "TA_Bad_3.txt", "TA_Bad_4.txt"]
bedroomFiles = ["TA_Schlafen_1.txt", "TA_Schlafen_2.txt", "TA_Schlafen_3.txt" ,"TA_Schlafen_4.txt"]
livingroomFiles = ["TA_Wohnen_1.txt", "TA_Wohnen_2.txt", "TA_Wohnen_3.txt" ,"TA_Wohnen_4.txt"]

def readAndMeregeSensorFiles(paths: list):
  sensor = None
  header_list = ["dateTime"]
  for x in range(len(paths)):
    header_list.append("part_" + str(x))
  for i, file in enumerate(paths):
    header = [header_list[0], header_list[i+1]]
    temp = pd.read_csv("data/" + file, sep="\t", decimal=".", names=header, skiprows=1)
    temp.index = pd.to_datetime(temp["dateTime"])
    temp = temp.drop(columns=["dateTime"])
    if sensor is None:
      sensor = temp
    else:
      sensor = pd.merge_ordered(sensor, temp, left_on = "dateTime", right_on="dateTime", how='outer', fill_method='ffill')
  sensor = sensor.fillna(0)
  sensor = sensor.set_index('dateTime')
  column_list = list(sensor)
  sensor['value'] = sensor[column_list].sum(axis=1) 
  sensor.loc[sensor['value'] > 1, 'value'] = 1
  return sensor

bathroom = readAndMeregeSensorFiles(bathroomFiles)
bedroom = readAndMeregeSensorFiles(bedroomFiles)
livingroom= readAndMeregeSensorFiles(livingroomFiles)
rooms = {"bedroom": bedroom, "livingroom": livingroom, "bathroom": bathroom, }

##Functions declaring

In [ ]:
#@title declare General functions

def getDataFrameByValue(df: pd.DataFrame, value):
  temp = df.copy()
  return temp.loc[temp['value'] == value]

def calculteTimeDelta(df):
  df = df.reset_index()
  df['Delta'] = (df['dateTime']-df['dateTime'].shift())
  df['Delta'] = df['Delta'].shift(-1).dt.total_seconds()
  df = df.rename(columns={'Delta': 'duration_in_s'})
  df = df.set_index('dateTime')
  return df

def filterRoom(df: pd.DataFrame, column_name):
  temp = df.copy()
  temp["shifted"] = temp[column_name].shift(1)
  temp["shifted"][0]=2 # first one should not be removed
  temp["change"] = abs(temp["shifted"] - temp [column_name])
  temp = temp[temp["change"] != 0]
  temp = calculteTimeDelta(temp[column_name])
  temp = temp.rename(columns={column_name:"value"})
  return temp

In [ ]:
##@title declare Rastering Functions -> 
##@markdown scaleToUltimateRoom(room, column, bucketTimeInMin) <- it's the ultimate function

def removeSameFollowValues(df: pd.DataFrame, column_name):
  temp = df.copy()
  temp["shifted"] = temp[column_name].shift(1)
  temp["shifted"][0]=2 # first one should not be removed
  temp["change"] = abs(temp["shifted"] - temp [column_name])
  temp = temp[temp["change"] != 0]
  temp = temp[column_name]
  return temp

def insertForgottenTimes(listOfDfs, timeInMin): 
  '''
    rastering a list of buckets 
  '''
  lastDf = None
  result = []
  for dfTuple in listOfDfs:
    #fill last value of df
    df = dfTuple[1]
    endTime = dfTuple[0] + pd.Timedelta(seconds=60*timeInMin)
    indexTimestap = df.tail(1).index
    df.loc[indexTimestap,'duration_in_s'] = (endTime - indexTimestap).total_seconds()
   
    #add first Value to df
    if lastDf is not None:
      lastEntryInLastDf = lastDf.tail(1)
      firstEntryInDf = df.head(1)
      if not firstEntryInDf.empty:
        #print((firstEntryInDf.index - dfTuple[0]).total_seconds())
        firstRowDf = pd.DataFrame([[dfTuple[0], lastEntryInLastDf.iloc[0]['value'], 0]], columns=['dateTime','value','duration_in_s'])
        firstRowDf.loc[0,'duration_in_s'] = (firstEntryInDf.index - dfTuple[0]).total_seconds()
      else:
        firstRowDf = pd.DataFrame([[dfTuple[0], lastEntryInLastDf.iloc[0]['value'], (dfTuple[0] + pd.Timedelta(seconds=60*timeInMin) - dfTuple[0]).total_seconds()]], columns=['dateTime','value','duration_in_s'])
      firstRowDf = firstRowDf.set_index('dateTime')
      df = firstRowDf.append(df)

    result.append(df)
    lastDf = df
  return result

def splitIntoListOfBuckets(df: pd.DataFrame, timeInMin):
  tuples = list(tuple(df.resample(str(timeInMin)+'Min')))
  result = []
  for tup in tuples:
    df = calculteTimeDelta(tup[1].to_frame())
    result.append((tup[0], df))
  return insertForgottenTimes(result, timeInMin)

def filterRoomWithBuckets(room: pd.DataFrame, column, bucketTimeInMin):
  return splitIntoListOfBuckets(removeSameFollowValues(room, column), bucketTimeInMin)

def scaleToUltimateRoom(room: pd.DataFrame, column, bucketTimeInMin):
  listOfBuckets = filterRoomWithBuckets(room, column, bucketTimeInMin)
  ultimateDf = None
  for df in listOfBuckets:
    if ultimateDf is None:
      ultimateDf = df
    else:
      ultimateDf = ultimateDf.append(df)
  return ultimateDf

#Analysis


In [ ]:
#@title Room Data based on time

tempBathroom = bathroom.copy()
tempBathroom["value"] = 2* bathroom["value"]

tempbedroom = bedroom.copy()
tempbedroom["value"] = 3 * bedroom["value"]

# plotly
fig = go.Figure()
fig.add_trace(go.Scatter(x=tempBathroom.reset_index()["dateTime"], y=tempBathroom["value"], name="bathroom", line_shape='hv'))
fig.add_trace(go.Scatter(x=tempbedroom.reset_index()["dateTime"], y=tempbedroom["value"], name="bedroom", line_shape='hv'))
fig.add_trace(go.Scatter(x=livingroom.reset_index()["dateTime"], y=livingroom["value"], name="livingroom", line_shape='hv'))

fig.update_layout(title='Sensor activation by room',
                   xaxis_title='Datetime',
                   yaxis_title='Sensor activation (0 = off, 1,2,3 = on)')
fig.show()



In [ ]:
#@title Interactive heatmap based on rooms
heatMapLayout = "sideBySide" #@param ["sideBySide", "fullWidth"] {type:"string"}

def createHeatMap(name, df):
  heatMapGroup = filterRoom(df, "value").resample('H').count()
  heatMapGroup = heatMapGroup.reset_index()
  fig = go.Heatmap(
          z=heatMapGroup['value'],
          x=heatMapGroup['dateTime'].dt.time,
          y=heatMapGroup['dateTime'].dt.date,
          colorbar = dict(title='Activation Count'),
          colorscale='deep')
  return fig

def createHeatMapForDuration(name, df):
  heatMapGroup = getDataFrameByValue(scaleToUltimateRoom(df, "value", 60), 1).resample('H').sum()
  heatMapGroup = heatMapGroup.reset_index()
  fig = go.Heatmap(
      z=heatMapGroup['duration_in_s'],
      x=heatMapGroup['dateTime'].dt.time,
      y=heatMapGroup['dateTime'].dt.date,
      colorbar = dict(title='Duration Sum'),
      colorscale='deep'
  )
  return fig

if heatMapLayout is "sideBySide":
  plotTitles = []
  for key, value in rooms.items():
    plotTitles.append('Sensor activation duration heatmap of '+ key)
    plotTitles.append('Sensor activation count heatmap of '+ key)

  heatFig = make_subplots(
      rows=3, 
      cols=2,
      subplot_titles = plotTitles,
      shared_xaxes=True,
      vertical_spacing=0.05)

  i = 1
  for key, value in rooms.items():
    heatFig.add_trace(createHeatMapForDuration(key, value), row=i, col=1)
    heatFig.add_trace(createHeatMap(key, value), row=i, col=2)
    i=i+1

  heatFig.update_layout(
      height=800,
      xaxis_title='Hour',
      yaxis_title='Day',
      title="Room Heatmap comparison between activation count and sum of durations")
  heatFig.show()
elif heatMapLayout is "fullWidth":
  for key, value in rooms.items():
    fig = go.Figure(createHeatMapForDuration(key, value))
    fig.update_layout(title='Sensor activation duration heatmap of '+ key,
                 xaxis_title='Hour',
                 yaxis_title='Day')
    fig.show()
    fig = go.Figure(createHeatMap(key, value))
    fig.update_layout(title='Sensor activation count heatmap of '+ key,
                 xaxis_title='Hour',
                 yaxis_title='Day')
    fig.show()
    

In [ ]:
#@title Room Selection { vertical-output: true }
selectedRoomOption = "bedroom" #@param ["bathroom", "bedroom", "livingroom"] {type:"string"}
selectedRoom = (selectedRoomOption, rooms[selectedRoomOption])

In [ ]:
#@title Customizable Histogram
#@markdown Choose 1 of 5 normalizations
#@markdown * None = no normalization
#@markdown * percent = percentage (0–100%) of the total value in the bin
#@markdown * probability = fraction (0–1) of the total in the bin
#@markdown * density = aggregate divided by total (the sum of all bar areas equals the total number of sample points)
#@markdown * probability density = the output of histfunc for a given bin is normalized such that it corresponds to the probability that a random event whose distribution is described by the output of histfunc will fall into that bin (the sum of all bar areas equals 1)

histNormalization = "" #@param ["", "percent", "probability", "density", "probability density"] {type:"string"}

#@markdown Choose a fitting histogram bin size in hours (can be set to any number or from a suggested list)
histBinSizeInHours =  1#@param ["6", "12", "24"] {type:"raw", allow-input: true}
binSize = histBinSizeInHours * 60 #to millisec
#@markdown Note: histogram seems to not work of hour bins which are multiples of 5   ¯\\_(ツ)_/¯

##############################################
# the following code could be made easier with plotly express (see the following 2 lines)
#hist = filterRoom(selectedRoom[1], "value").reset_index()
#fig = px.histogram(hist, x="dateTime", y="duration_in_s", histfunc='sum', color='value')
##############################################
fig = go.Figure()
ultimateDf = scaleToUltimateRoom(selectedRoom[1], "value", binSize)

histVal0 = getDataFrameByValue(ultimateDf, 0)
histVal1 = getDataFrameByValue(ultimateDf, 1)
trace0 = go.Histogram(x=histVal0.reset_index()['dateTime'], 
                      y=histVal0['duration_in_s']/60,
                      histfunc='sum',
                      histnorm=histNormalization,
                      xbins=dict(size=str(binSize * 60000)),
                      autobinx=False,
                      name="0.0"
                     )
trace1 = go.Histogram(x=histVal1.reset_index()['dateTime'],
                      y=histVal1['duration_in_s']/60,
                      histfunc='sum',
                      histnorm=histNormalization,
                      xbins=dict(size=str(binSize* 60000)),
                      autobinx=False,
                      name="1.0"
                     )
fig.update_layout(title="Histogram of "+selectedRoom[0]+" with "+str(histBinSizeInHours)+"h bin size and normalization option: "+(histNormalization or "None"),
                  xaxis_title="Date",
                  yaxis_title="Value Duration in minutes with normalization: "+(histNormalization or "None"),
                  barmode='stack')
fig.add_trace(trace1)
fig.add_trace(trace0)
fig.show()
ultimateDf

value  duration_in_s
dateTime                                     
2018-05-16 22:48:20.589    1.0          3.032
2018-05-16 22:48:23.621    0.0         11.991
2018-05-16 22:48:35.612    1.0          1.010
2018-05-16 22:48:36.622    0.0        683.378
2018-05-16 23:00:00.000    0.0       3600.000
...                        ...            ...
2018-05-24 12:16:28.846    0.0       1154.313
2018-05-24 12:35:43.159    1.0         11.050
2018-05-24 12:35:54.209    0.0         77.008
2018-05-24 12:37:11.217    1.0          5.014
2018-05-24 12:37:16.231    0.0       1363.769

[3422 rows x 2 columns]

# Playground


In [ ]:
#@title Calc buckets in min (long task if files doesn't exist)

if Path("bedroomInMin.csv").is_file():
  bedroomInMin = pd.read_csv("bedroomInMin.csv")
  bedroomInMin["dateTime"] = pd.to_datetime(bedroomInMin["dateTime"])
  bedroomInMin = bedroomInMin.set_index("dateTime")
else:
  bedroomInMin = scaleToUltimateRoom(bedroom, "value", 1)
  bedroomInMin.to_csv("bedroomInMin.csv")

if Path("bathroomInMin.csv").is_file():
  bathroomInMin = pd.read_csv("bathroomInMin.csv")
  bathroomInMin["dateTime"] = pd.to_datetime(bathroomInMin["dateTime"])
  bathroomInMin = bathroomInMin.set_index("dateTime")
else:
  bathroomInMin = scaleToUltimateRoom(bathroom, "value", 1)
  bathroomInMin.to_csv("bathroomInMin.csv")

if Path("livingRoomInMin.csv").is_file():
  livingRoomInMin = pd.read_csv("livingRoomInMin.csv")
  livingRoomInMin["dateTime"] = pd.to_datetime(livingRoomInMin["dateTime"])
  livingRoomInMin = livingRoomInMin.set_index("dateTime")
else:
  livingRoomInMin = scaleToUltimateRoom(livingroom, "value", 1)
  livingRoomInMin.to_csv("livingRoomInMin.csv")
print(bedroomInMin)
print(bathroomInMin)
print(livingRoomInMin)


                         value  duration_in_s
dateTime                                     
2018-05-16 22:48:20.589    1.0          3.032
2018-05-16 22:48:23.621    0.0         11.991
2018-05-16 22:48:35.612    1.0          1.010
2018-05-16 22:48:36.622    0.0         23.378
2018-05-16 22:49:00.000    0.0         60.000
...                        ...            ...
2018-05-24 12:35:54.209    0.0          5.791
2018-05-24 12:36:00.000    0.0         60.000
2018-05-24 12:37:00.000    0.0         11.217
2018-05-24 12:37:11.217    1.0          5.014
2018-05-24 12:37:16.231    0.0         43.769

[14149 rows x 2 columns]
                         value  duration_in_s
dateTime                                     
2018-05-17 00:33:30.943    1.0          1.000
2018-05-17 00:33:31.943    0.0          1.012
2018-05-17 00:33:32.955    1.0         11.018
2018-05-17 00:33:43.973    0.0         16.027
2018-05-17 00:34:00.000    0.0          6.943
...                        ...            ...
2018-05-

In [ ]:
#print(bedroomInMin)
#print(bathroomInMin)
#print(livingRoomInMin)

def calcSumAndGetSeries(df):
  df = df.loc[df['value'] == 1]
  temp = df.groupby(['value']).sum()["duration_in_s"]
  return temp

startDate = bedroomInMin.head(1).append(livingRoomInMin.head(1)).append(bathroomInMin.head(1)).index.max().replace(second=0, microsecond=0)
endDate = bedroomInMin.tail(1).append(livingRoomInMin.tail(1)).append(bathroomInMin.tail(1)).index.min().replace(second=0, microsecond=0)
timeDifference = ((endDate - startDate).total_seconds() / 60)

ultimateDf = pd.DataFrame(columns=["bathroom", "bedroom", "livingRoom"]);
for i in range(0,round(difference)+1):
  newDf = pd.DataFrame()
  currentTime = startDate + pd.Timedelta(minutes=i)

  bedroomMin = calcSumAndGetSeries(bedroomInMin.loc[currentTime:currentTime+pd.Timedelta(minutes=1)-pd.Timedelta(microseconds=1)])
  if bedroomMin.count() > 0:
    newDf = newDf.assign(bedroom=bedroomMin.values)

  bathroomMin = calcSumAndGetSeries(bathroomInMin.loc[currentTime:currentTime+pd.Timedelta(minutes=1)-pd.Timedelta(microseconds=1)])
  if bathroomMin.count() > 0:
    newDf = newDf.assign(bathroom= bathroomMin.values)
 
  livingRoomMin = calcSumAndGetSeries(livingRoomInMin.loc[currentTime:currentTime+pd.Timedelta(minutes=1)-pd.Timedelta(microseconds=1)])
  if livingRoomMin.count() > 0:
    newDf = newDf.assign(livingRoom= livingRoomMin.values)
  
  newDf = newDf.assign(dateTime = currentTime)
  newDf = newDf.set_index("dateTime")
  ultimateDf = ultimateDf.append(newDf)
print(ultimateDf)

                     bathroom  bedroom  livingRoom
2018-05-17 00:33:00    12.018   15.001      13.021
2018-05-17 00:34:00    16.991      NaN       0.992
2018-05-17 00:35:00       NaN   14.967      21.987
2018-05-17 00:44:00       NaN    4.062         NaN
2018-05-17 00:47:00       NaN    2.973         NaN
...                       ...      ...         ...
2018-05-24 12:16:00       NaN   24.845      18.173
2018-05-24 12:17:00       NaN      NaN      19.885
2018-05-24 12:18:00    11.641      NaN      19.433
2018-05-24 12:19:00    16.920      NaN         NaN
2018-05-24 12:20:00    31.509      NaN       1.424

[2884 rows x 3 columns]


In [ ]:
fil = filterRoomWithBuckets(selectedRoom[1], 'value', 24*60)
daily6h15Min = []
for df in fil:
  for ddf in filterRoomWithBuckets(df, 'value', 6*60):
    #px.histogram(ddf, x=ddf.index, y="duration_in_s", histfunc='sum', color='value').show()
    
    daily6h15Min.append(scaleToUltimateRoom(ddf, 'value', 60))
    #px.box(ddf.reset_index(), x=ddf.index.hour, y=ddf["duration_in_s"], color='value').show()

#fig = make_subplots(rows=(len(daily6h15Min)-1)%4, cols=4)
#i = 0
#for bucket in daily6h15Min[1:]:
#  px.histogram(bucket.reset_index(), x="dateTime", y="duration_in_s", histfunc='sum', color='value', nbins=24).show()
for bucket in daily6h15Min[:5]:
  f=px.box(bucket.reset_index(), x=bucket.index.hour, y="duration_in_s", color='value')
  f.update_layout(width=1000)
  f.show()

#df = px.data.tips()
#print(df)
#fig = px.box(df, x="time", y="total_bill")
#fig.show()

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:7: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
# add new row for scatter 
kelDf = None
for key, value in rooms.items():
  if kelDf is None:
    kelDf = value
    kelDf['room'] = key
    kelDf['time'] = kelDf.index.hour
  else:
    tempDf = value
    tempDf['room'] = key
    tempDf['time'] = tempDf.index.hour
    kelDf = kelDf.append(tempDf)


kelDf = calculteTimeDelta(kelDf)
kelDf
fig = px.scatter_matrix(kelDf,
    dimensions=["duration_in_s", "time", "value"],
    color="room")
fig.show()




In [ ]:
# df = pd.DataFrame([
#     dict(Task="Job A", Start='2009-01-01', Finish='2009-02-28'),
#     dict(Task="Job B", Start='2009-03-05', Finish='2009-04-15'),
#     dict(Task="Job C", Start='2009-02-20', Finish='2009-05-30')
# ])

#fig = px.timeline(kelDf, x_start=keldDf.reset_index()["dateTime"], x_end=keldDf.reset_index()["dateTime"] + kelDf["duration_in_s"], y="room", color="value")
#fig.update_yaxes(autorange="reversed") # otherwise tasks are listed from the bottom up
#fig.show()
#df = pd.DataFrame([
#    dict(Task="Job A", Start='2009-01-01', Finish='2009-02-28'),
#    dict(Task="Job B", Start='2009-03-05', Finish='2009-04-15'),
#    dict(Task="Job C", Start='2009-02-20', Finish='2009-05-30')
#])
#
#fig = px.timeline(df, x_start="Start", x_end="Finish", y="Task")
#fig.update_yaxes(autorange="reversed") # otherwise tasks are listed from the bottom up
#fig.show()